In [26]:
import os
import cv2
import re
import numpy as np
import radiomics
from radiomics import featureextractor
from PIL import Image
import SimpleITK as sitk
import pandas as pd
from collections import Counter
from imutils import paths
import random



In [27]:
DATASET_PATH = "../Datasets/OrigDataset"
SEG_PATH = "../Datasets/new_data"
CSV_FILE_PATH = os.path.join(DATASET_PATH, "GroundTruth.csv")
# define the path to the images and masks dataset
IMAGE_DATASET_PATH = os.path.join(SEG_PATH, "images/")
MASK_DATASET_PATH = os.path.join(SEG_PATH, "masks/")

# Type of tumor
melanoma = []
nevus = []
basal_cell_carcinoma = []
actinic_keratoses_and_intraepithelial_carcinoma = []
benign_keratosis_like_lesions = []
dermatofibroma  = []
vascular_lesion = []

lesion_dict = {
    "MEL": 0, 
    "NV": 1,
    "BCC": 2,
    "AKIEC": 3,
    "BKL": 4,
    "DF": 5,
    "VASC": 6
}


params = 'Params.yaml'


In [28]:
imagePaths = sorted(list(paths.list_images(IMAGE_DATASET_PATH)))
maskPaths = sorted(list(paths.list_images(MASK_DATASET_PATH)))


In [29]:
# Function to convert
def listToString(s):
 
    # initialize an empty string
    str1 = " "
 
    # return string
    return (str1.join(s))


In [30]:
df = pd.read_csv(CSV_FILE_PATH)


In [31]:
extractor = featureextractor.RadiomicsFeatureExtractor(params)
results = []
categories = []

for i in range(len(imagePaths)):
    path_original = imagePaths[i]
    path_label = maskPaths[i]
    original = cv2.imread(path_original)
    # Extract chann
    b, g, r = cv2.split(original)
    blue_channel_2d = b.copy()

    original = Image.fromarray(blue_channel_2d)
    original.save("original.png")

    label = cv2.imread(path_label, 0)
    label = Image.fromarray(label, "L")
    label.save("label.png")
    result = extractor.execute("original.png", path_label)
    results.append(result)
    
    # Find part of a string that starts with "ISIC_" and ends with number or numbers
    name = re.findall(r"ISIC_\d+", imagePaths[i])
    
    # Select a row that has given name in column names
    row = df.loc[df['image'] == listToString(name)]

    column_name = None
    
    # Iterate through the columns in the subset to find the matching value
    for col in row.columns:
        if 1.0 in row[col].values:
            column_name = col
            break
    
    # Append it to a list of categories
    categories.append(lesion_dict[column_name])
    
feature_names = list(sorted(filter ( lambda k: k.startswith("original_"), results[0] )))


GLCM is symmetrical, therefore Sum Average = 2 * Joint Average, only 1 needs to be calculated
GLCM is symmetrical, therefore Sum Average = 2 * Joint Average, only 1 needs to be calculated
GLCM is symmetrical, therefore Sum Average = 2 * Joint Average, only 1 needs to be calculated
GLCM is symmetrical, therefore Sum Average = 2 * Joint Average, only 1 needs to be calculated
GLCM is symmetrical, therefore Sum Average = 2 * Joint Average, only 1 needs to be calculated
GLCM is symmetrical, therefore Sum Average = 2 * Joint Average, only 1 needs to be calculated
GLCM is symmetrical, therefore Sum Average = 2 * Joint Average, only 1 needs to be calculated
GLCM is symmetrical, therefore Sum Average = 2 * Joint Average, only 1 needs to be calculated
GLCM is symmetrical, therefore Sum Average = 2 * Joint Average, only 1 needs to be calculated
GLCM is symmetrical, therefore Sum Average = 2 * Joint Average, only 1 needs to be calculated
GLCM is symmetrical, therefore Sum Average = 2 * Joint Avera

In [32]:
samples = np.zeros((len(imagePaths),len(feature_names)))
for case_id in range(0 ,len(imagePaths)):
    a = np.array([])
    for feature_name in feature_names:
        a = np.append(a, results[case_id][feature_name])
    samples[case_id,:] = a
    
# May have NaNs
samples = np.nan_to_num(samples)


In [33]:
len(imagePaths)


60078

In [34]:
len(samples)


60078

In [35]:
len(categories)


60078

In [36]:
Counter(categories)


Counter({1: 40230, 0: 6672, 4: 6588, 2: 3084, 3: 1962, 6: 852, 5: 690})

In [37]:
new_lesion_dict = {
    0: [], 
    1: [],
    2: [],
    3: [],
    4: [],
    5: [],
    6: []
}


length_cat = len(categories)
for i in range(length_cat):
    new_lesion_dict[categories[i]].append(samples[i])
        

In [38]:
X =[]
y = []
for category in new_lesion_dict:
    for i in range(len(new_lesion_dict[category])):
        X.append(new_lesion_dict[category][i])
        y.append(category)
        


In [39]:
df_to_save = pd.DataFrame()


In [40]:
column_names = feature_names.copy()


In [41]:
column_names.append('categories')


In [42]:
for col in column_names:
    df_to_save[col] = []
    

/var/folders/8m/1npctfws7dnc_lbx3mhg9kdc0000gn/T/ipykernel_1038/769385081.py:2: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  df_to_save[col] = []
/var/folders/8m/1npctfws7dnc_lbx3mhg9kdc0000gn/T/ipykernel_1038/769385081.py:2: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  df_to_save[col] = []
/var/folders/8m/1npctfws7dnc_lbx3mhg9kdc0000gn/T/ipykernel_1038/769385081.py:2: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider join

In [43]:
df_to_save


Empty DataFrame
Columns: [original_firstorder_10Percentile, original_firstorder_90Percentile, original_firstorder_Energy, original_firstorder_Entropy, original_firstorder_InterquartileRange, original_firstorder_Kurtosis, original_firstorder_Maximum, original_firstorder_Mean, original_firstorder_MeanAbsoluteDeviation, original_firstorder_Median, original_firstorder_Minimum, original_firstorder_Range, original_firstorder_RobustMeanAbsoluteDeviation, original_firstorder_RootMeanSquared, original_firstorder_Skewness, original_firstorder_TotalEnergy, original_firstorder_Uniformity, original_firstorder_Variance, original_glcm_Autocorrelation, original_glcm_ClusterProminence, original_glcm_ClusterShade, original_glcm_ClusterTendency, original_glcm_Contrast, original_glcm_Correlation, original_glcm_DifferenceAverage, original_glcm_DifferenceEntropy, original_glcm_DifferenceVariance, original_glcm_Id, original_glcm_Idm, original_glcm_Idmn, original_glcm_Idn, original_glcm_Imc1, original_glcm_Imc2, original_glcm_InverseVariance, original_glcm_JointAverage, original_glcm_JointEnergy, original_glcm_JointEntropy, original_glcm_MCC, original_glcm_MaximumProbability, original_glcm_SumAverage, original_glcm_SumEntropy, original_glcm_SumSquares, original_gldm_DependenceEntropy, original_gldm_DependenceNonUniformity, original_gldm_DependenceNonUniformityNormalized, original_gldm_DependenceVariance, original_gldm_GrayLevelNonUniformity, original_gldm_GrayLevelVariance, original_gldm_HighGrayLevelEmphasis, original_gldm_LargeDependenceEmphasis, original_gldm_LargeDependenceHighGrayLevelEmphasis, original_gldm_LargeDependenceLowGrayLevelEmphasis, original_gldm_LowGrayLevelEmphasis, original_gldm_SmallDependenceEmphasis, original_gldm_SmallDependenceHighGrayLevelEmphasis, original_gldm_SmallDependenceLowGrayLevelEmphasis, original_glrlm_GrayLevelNonUniformity, original_glrlm_GrayLevelNonUniformityNormalized, original_glrlm_GrayLevelVariance, original_glrlm_HighGrayLevelRunEmphasis, original_glrlm_LongRunEmphasis, original_glrlm_LongRunHighGrayLevelEmphasis, original_glrlm_LongRunLowGrayLevelEmphasis, original_glrlm_LowGrayLevelRunEmphasis, original_glrlm_RunEntropy, original_glrlm_RunLengthNonUniformity, original_glrlm_RunLengthNonUniformityNormalized, original_glrlm_RunPercentage, original_glrlm_RunVariance, original_glrlm_ShortRunEmphasis, original_glrlm_ShortRunHighGrayLevelEmphasis, original_glrlm_ShortRunLowGrayLevelEmphasis, original_glszm_GrayLevelNonUniformity, original_glszm_GrayLevelNonUniformityNormalized, original_glszm_GrayLevelVariance, original_glszm_HighGrayLevelZoneEmphasis, original_glszm_LargeAreaEmphasis, original_glszm_LargeAreaHighGrayLevelEmphasis, original_glszm_LargeAreaLowGrayLevelEmphasis, original_glszm_LowGrayLevelZoneEmphasis, original_glszm_SizeZoneNonUniformity, original_glszm_SizeZoneNonUniformityNormalized, original_glszm_SmallAreaEmphasis, original_glszm_SmallAreaHighGrayLevelEmphasis, original_glszm_SmallAreaLowGrayLevelEmphasis, original_glszm_ZoneEntropy, original_glszm_ZonePercentage, original_glszm_ZoneVariance, original_ngtdm_Busyness, original_ngtdm_Coarseness, original_ngtdm_Complexity, original_ngtdm_Contrast, original_ngtdm_Strength, original_shape2D_Elongation, original_shape2D_MajorAxisLength, original_shape2D_MaximumDiameter, original_shape2D_MeshSurface, original_shape2D_MinorAxisLength, original_shape2D_Perimeter, original_shape2D_PerimeterSurfaceRatio, ...]
Index: []

[0 rows x 103 columns]

In [44]:
list_of_arrays = X.copy()
single_list = y.copy()


In [45]:
len(list_of_arrays[0])


102

In [46]:
for i in range(len(list_of_arrays)):
    list_of_arrays[i] = np.append(list_of_arrays[i], single_list[i])


In [47]:
len(list_of_arrays[0])


103

In [48]:
for array in list_of_arrays:
    #list_of_arrays[i] = pd.concat([list_of_arrays[i], pd.DataFrame([array])], ignore_index=True)
    #list_of_arrays[i] = pd.concat([list_of_arrays[i], pd.Series(single_list[i])])
    
    
    df_to_save = pd.concat([df_to_save, pd.DataFrame([array], columns=df_to_save.columns)], ignore_index=True)
    #df.append(pd.DataFrame([array], columns=df.columns), ignore_index=True)
    
    #df = df.append(pd.DataFrame([array], columns=df.columns), ignore_index=True)
    #df_to_save = df_to_save.append(pd.DataFrame([array], columns=df_to_save.columns), ignore_index=True)
    

In [49]:
df_to_save


original_firstorder_10Percentile  original_firstorder_90Percentile  \
0                                  47.0                             138.0   
1                                  47.0                             138.0   
2                                  48.0                             135.0   
3                                  47.0                             137.0   
4                                  47.0                             138.0   
...                                 ...                               ...   
60073                             118.0                             189.0   
60074                             118.0                             189.0   
60075                             121.0                             191.0   
60076                             118.0                             189.0   
60077                             118.0                             189.0   

       original_firstorder_Energy  original_firstorder_Entropy  \
0                     553402263.0                     2.426495   
1                     553402263.0                     2.426495   
2                     531940492.0                     2.387911   
3                     607862880.0                     2.406654   
4                     553238892.0                     2.421444   
...                           ...                          ...   
60073                 913954053.0                     2.324428   
60074                 913713002.0                     2.322281   
60075                 911688906.0                     2.307631   
60076                 913805301.0                     2.323986   
60077                 913748145.0                     2.321006   

       original_firstorder_InterquartileRange  original_firstorder_Kurtosis  \
0                                        53.0                      2.875234   
1                                        53.0                      2.875234   
2                                        51.0                      2.913036   
3                                        52.0                      2.809334   
4                                        53.0                      2.880165   
...                                       ...                           ...   
60073                                    35.0                      6.360038   
60074                                    35.0                      6.384839   
60075                                    36.0                      6.246678   
60076                                    35.0                      6.376840   
60077                                    35.0                      6.381200   

       original_firstorder_Maximum  original_firstorder_Mean  \
0                            248.0                 85.178875   
1                            248.0                 85.178875   
2                            245.0                 84.279150   
3                            238.0                 84.834237   
4                            245.0                 85.166308   
...                            ...                       ...   
60073                        234.0                153.715448   
60074                        232.0                153.697632   
60075                        222.0                154.946632   
60076                        234.0                153.700146   
60077                        232.0                153.695928   

       original_firstorder_MeanAbsoluteDeviation  original_firstorder_Median  \
0                                      29.364067                        76.0   
1                                      29.364067                        76.0   
2                                      28.502673                        75.0   
3                                      29.133316                        75.0   
4                                      29.354522                        76.0   
...                                          ...                         ...   
60073      

In [50]:
df_to_save.to_csv('../Datasets/AllForSelection_blue.csv')
